read json

In [4]:
df = (spark.read \
        .option('inferSchema', 'true') \
        .json('abfss://asa-kz@asadatalake19hvmew.dfs.core.windows.net/online-user-profiles-02/*.json', multiLine=True)
    )

df.printSchema()

StatementMeta(SparkPool01, 30, 4, Finished, Available)

root
 |-- topProductPurchases: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- itemsPurchasedLast12Months: long (nullable = true)
 |    |    |-- productId: long (nullable = true)
 |-- visitorId: long (nullable = true)



In [5]:
df.createOrReplaceTempView("user_profiles")

StatementMeta(SparkPool01, 30, 5, Finished, Available)

In [6]:
%%sql

SELECT * FROM user_profiles LIMIT 10

StatementMeta(SparkPool01, 30, 6, Finished, Available)

<Spark SQL result set with 10 rows and 2 fields>

explode json 

In [7]:
from pyspark.sql.functions import udf, explode

flat=df.select('visitorId',explode('topProductPurchases').alias('topProductPurchases_flat'))
#flat.show(100)

StatementMeta(SparkPool01, 30, 7, Finished, Available)

In [8]:
topPurchases = (flat.select('visitorId','topProductPurchases_flat.productId','topProductPurchases_flat.itemsPurchasedLast12Months')
    .orderBy('visitorId'))

#topPurchases.show(10)
df.createOrReplaceTempView("topPurchases")

StatementMeta(SparkPool01, 30, 8, Finished, Available)

In [9]:
# order  
sortedTopPurchases = topPurchases.orderBy("itemsPurchasedLast12Months")
display(sortedTopPurchases.limit(10))
df.createOrReplaceTempView("sortedTopPurchases")

StatementMeta(SparkPool01, 30, 9, Finished, Available)

SynapseWidget(Synapse.DataFrame, 1a9e9b57-b3bb-4368-a98e-931170d3f673)

In [13]:
from pyspark.sql.functions import *
sortedTopPurchasesDesc = (topPurchases.orderBy( col("itemsPurchasedLast12Months").desc() ))
display(sortedTopPurchasesDesc.limit(10))

StatementMeta(SparkPool01, 30, 13, Finished, Available)

SynapseWidget(Synapse.DataFrame, 1d4c7afb-9f63-4009-a038-5e24c9927485)

In [14]:
%%sql 
select * from topPurchases

StatementMeta(SparkPool01, 30, 14, Finished, Available)

<Spark SQL result set with 1000 rows and 2 fields>

count purchases for each visitor

In [15]:
#10
groupedTopPurchases = (sortedTopPurchases.select("visitorId")
    .groupBy("visitorId")
    .agg(count("*").alias("total"))
    .orderBy("visitorId") )

display(groupedTopPurchases.limit(100))

StatementMeta(SparkPool01, 30, 15, Finished, Available)

SynapseWidget(Synapse.DataFrame, ff93d71a-acc5-4b52-81f9-5e67284abb26)

In [16]:
groupedTopPurchases = (sortedTopPurchases.select("visitorId","itemsPurchasedLast12Months")
    .groupBy("visitorId")
    .agg(sum("itemsPurchasedLast12Months").alias("totalItemsPurchased"))
    .orderBy("visitorId") )

display(groupedTopPurchases.limit(100))

StatementMeta(SparkPool01, 30, 16, Finished, Available)

SynapseWidget(Synapse.DataFrame, ea40dd4e-8edc-4186-8a8e-f64f21bc7333)

In [17]:
%%pyspark
import uuid
# Generate random GUID
runId = uuid.uuid4()
groupedTopPurchases.write.parquet('abfss://asa-kz@asadatalake19hvmew.dfs.core.windows.net/top-purchases/' + str(runId) + '.parquet')

StatementMeta(SparkPool01, 30, 17, Finished, Available)